In [1]:
import numpy as np

import sys
sys.path.append("../")
from koopmanlib.dictionary import PsiNN

In [2]:
basis_function = PsiNN(layer_sizes=[100,100,100], n_psi_train=22)

In [3]:
from duffing_oscillator import duffing_oscillator
from scipy.integrate import solve_ivp

# Parameters
delta = 0.5
alpha = -1
beta = 1

# Sample N=1000 initial points, with uniform distribution [-2, 2].
N = 1000
np.random.seed(39)
sample_data_x0 = (np.random.rand(N, 2) * 4) - 2

tspan = [0, 2.5]
nstep = 11
data = np.zeros((N, 2, nstep))

t_eval = np.linspace(tspan[0], tspan[1], nstep)

for idx, x0 in enumerate(sample_data_x0):
    sol = solve_ivp(duffing_oscillator, tspan, x0, t_eval=t_eval, args=(delta, alpha, beta))
    data[idx, 0, :] = sol.y[0]
    data[idx, 1, :] = sol.y[1]

# Pairwise shifted data X and Y
X = data[:, :, :-1] # shape: (1000, 2, 10)
Y = data[:, :, 1:]

# Transpose and reshape the data.
X = np.transpose(X, (0, 2, 1)).reshape(N * (nstep-1), 2) # shape: (10000, 2)
Y = np.transpose(Y, (0, 2, 1)).reshape(N * (nstep-1), 2)

In [4]:
len_all = X.shape[0]
data_x_train = X[:int(0.7*len_all),:]
data_x_valid = X[int(0.7*len_all)+1:,:]

data_y_train = Y[:int(0.7*len_all),:]
data_y_valid = Y[int(0.7*len_all)+1:,:]

In [5]:
data_train = [data_x_train, data_y_train]
data_valid = [data_x_valid, data_y_valid]

In [16]:
# Using solver0
from koopmanlib.solver_0 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 154ms/step - loss: 9.4125e-04 - val_loss: 0.0131
Epoch 2/2
2/2 [==============================] - 0s 34ms/step - loss: 0.0099 - val_loss: 0.0039
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 64ms/step - loss: 0.0015 - val_loss: 0.0065
Epoch 2/2
2/2 [==============================] - 0s 39ms/step - loss: 0.0050 - val_loss: 5.6011e-04
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 62ms/step - loss: 7.5630e-04 - val_loss: 0.0045
Epoch 2/2
2/2 [==============================] - 0s 38ms/step - loss: 0.0038 - val_loss: 3.1857e-04
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 61ms/step - loss: 4.4442e-04 - val_loss: 0.0026
Epoch 2/2
2/2 [==============================] - 0s 44ms/step - loss: 0.0022 - val_loss: 3.4062e-04
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 68ms/step - loss: 2.6740e-04 - val_loss: 0.

In [17]:
# Results from solver0
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs0 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs0['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs0['resDMD_DL_outputs']['efuns'].shape)

[1.00487727+0.j         1.00013922+0.j         0.80787982+0.16721902j
 0.80787982-0.16721902j 0.79757325+0.3251494j  0.79757325-0.3251494j
 0.74075842+0.j         0.69831386+0.41181313j 0.69831386-0.41181313j
 0.59980333+0.29130714j 0.59980333-0.29130714j 0.48249382+0.28546772j
 0.48249382-0.28546772j 0.21323682+0.j         0.20322769+0.28107633j
 0.20322769-0.28107633j 0.15489242-0.642556j   0.15489242+0.642556j
 0.11757473+0.j         0.05062814+0.j         0.00609103-0.0046907j
 0.00609103+0.0046907j  0.00128049+0.03860257j 0.00128049-0.03860257j
 0.00119958+0.j        ]
(10000, 25)


In [14]:
# Using solver1
from koopmanlib.solver_1 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 8s 1s/step - loss: 0.7570 - val_loss: 0.7617
Epoch 2/2
2/2 [==============================] - 0s 91ms/step - loss: 0.7620 - val_loss: 0.7551
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 113ms/step - loss: 0.7554 - val_loss: 0.7667
Epoch 2/2
2/2 [==============================] - 0s 104ms/step - loss: 0.7598 - val_loss: 0.7668
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 115ms/step - loss: 0.7648 - val_loss: 0.7652
Epoch 2/2
2/2 [==============================] - 0s 101ms/step - loss: 0.7583 - val_loss: 0.7553
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 115ms/step - loss: 0.7553 - val_loss: 0.7518
Epoch 2/2
2/2 [==============================] - 0s 96ms/step - loss: 0.7578 - val_loss: 0.7654
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 119ms/step - loss: 0.7566 - val_loss: 0.7571
Epoch 2/2
2/2 [=====

In [15]:
# Results from solver1
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs1 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs1['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs1['resDMD_DL_outputs']['efuns'].shape)

[ 0.99985181+0.j          0.99860672+0.j          0.82635589-0.24598346j
  0.82635589+0.24598346j  0.81590937-0.17039815j  0.81590937+0.17039815j
  0.79012009+0.j          0.69739887+0.31354006j  0.69739887-0.31354006j
  0.65971541-0.48026954j  0.65971541+0.48026954j  0.63322323+0.1812395j
  0.63322323-0.1812395j   0.34710939-0.45646995j  0.34710939+0.45646995j
  0.30352412-0.20846779j  0.30352412+0.20846779j  0.14939853+0.j
  0.11848239-0.63848541j  0.11848239+0.63848541j  0.05252129-0.02689364j
  0.05252129+0.02689364j -0.00261602-0.05018155j -0.00261602+0.05018155j
 -0.04453541+0.j        ]
(10000, 25)


In [12]:
# Using solver2
from koopmanlib.solver_2 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 244ms/step - loss: 97733.9029 - val_loss: 77631.2344
Epoch 2/2
2/2 [==============================] - 0s 72ms/step - loss: 96052.1797 - val_loss: 76948.0078
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 86ms/step - loss: 96487.9643 - val_loss: 76630.1328
Epoch 2/2
2/2 [==============================] - 0s 50ms/step - loss: 95369.0357 - val_loss: 76319.6875
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 81ms/step - loss: 95671.0569 - val_loss: 76039.3750
Epoch 2/2
2/2 [==============================] - 0s 50ms/step - loss: 95555.3783 - val_loss: 75833.8672
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 74ms/step - loss: 93982.8516 - val_loss: 75656.7500
Epoch 2/2
2/2 [==============================] - 0s 52ms/step - loss: 93985.7121 - val_loss: 75501.7422
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 99m

In [13]:
# Results from solver2
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs2 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs2['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs2['resDMD_DL_outputs']['efuns'].shape)

[1.00016281+0.j         0.91991028+0.1520683j  0.91991028-0.1520683j
 0.8149    +0.j         0.70885366+0.06127243j 0.70885366-0.06127243j
 0.68340871+0.30845087j 0.68340871-0.30845087j 0.47438702+0.25795209j
 0.47438702-0.25795209j 0.39430453-0.27777918j 0.39430453+0.27777918j
 0.23231904+0.30891841j 0.23231904-0.30891841j 0.2309976 +0.04216957j
 0.2309976 -0.04216957j 0.14338611+0.j         0.13980091-0.39793864j
 0.13980091+0.39793864j 0.09265332+0.j         0.04364049+0.j
 0.03529583+0.j         0.01168477+0.j         0.01031329+0.j
 0.00487244+0.j        ]
(10000, 25)


In [ ]:
# Using solver3
from koopmanlib.solver_3 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 218ms/step - loss: 0.0012 - val_loss: 3.8479e-04
Epoch 2/2
2/2 [==============================] - 0s 61ms/step - loss: 9.6430e-04 - val_loss: 0.0027
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 82ms/step - loss: 1.8491e-04 - val_loss: 1.6050e-04
Epoch 2/2
2/2 [==============================] - 0s 52ms/step - loss: 1.5864e-04 - val_loss: 2.5031e-04
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 72ms/step - loss: 1.0789e-04 - val_loss: 1.3379e-04
Epoch 2/2
2/2 [==============================] - 0s 45ms/step - loss: 1.1142e-04 - val_loss: 1.2994e-04
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 70ms/step - loss: 1.0430e-04 - val_loss: 1.2581e-04
Epoch 2/2
2/2 [==============================] - 0s 46ms/step - loss: 1.0754e-04 - val_loss: 1.2285e-04
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 70ms/step -

In [10]:
# Results from solver3
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs3 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs3['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs3['resDMD_DL_outputs']['efuns'].shape)

[ 1.00645975e+00+0.00000000e+00j  9.99997890e-01+0.00000000e+00j
  7.69214095e-01+2.05256200e-01j  7.69214095e-01-2.05256200e-01j
  6.72953185e-01+3.52249591e-01j  6.72953185e-01-3.52249591e-01j
  6.54608961e-01+0.00000000e+00j  5.52533616e-01+0.00000000e+00j
  4.47452913e-01+4.27361883e-01j  4.47452913e-01-4.27361883e-01j
  2.91639628e-01+0.00000000e+00j  1.13117056e-01+0.00000000e+00j
  7.33498416e-02+0.00000000e+00j  5.76241799e-02-4.68296169e-01j
  5.76241799e-02+4.68296169e-01j  2.78514582e-02+0.00000000e+00j
  2.28760285e-02+0.00000000e+00j  1.36069076e-03+0.00000000e+00j
  5.43123439e-04+0.00000000e+00j  1.03132556e-04+6.92709431e-05j
  1.03132556e-04-6.92709431e-05j -4.19603000e-04+1.68324740e-02j
 -4.19603000e-04-1.68324740e-02j -1.42686213e-03+2.35415472e-03j
 -1.42686213e-03-2.35415472e-03j]
(10000, 25)


In [7]:
# Using solver4
from koopmanlib.solver_4 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 4s 561ms/step - loss: 0.1170 - val_loss: 0.1059
Epoch 2/2
2/2 [==============================] - 0s 77ms/step - loss: 0.1370 - val_loss: 0.1014
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 96ms/step - loss: 0.1256 - val_loss: 0.0954
Epoch 2/2
2/2 [==============================] - 0s 76ms/step - loss: 0.1243 - val_loss: 0.1048
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 96ms/step - loss: 0.1188 - val_loss: 0.0803
Epoch 2/2
2/2 [==============================] - 0s 82ms/step - loss: 0.1093 - val_loss: 0.0787
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 99ms/step - loss: 0.1046 - val_loss: 0.0751
Epoch 2/2
2/2 [==============================] - 0s 76ms/step - loss: 0.0965 - val_loss: 0.0697
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 97ms/step - loss: 0.0884 - val_loss: 0.0716
Epoch 2/2
2/2 [========

In [8]:
# Results from solver4
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs4 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs4['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs4['resDMD_DL_outputs']['efuns'].shape)

[ 1.00000109e+00+0.00000000e+00j  9.95334491e-01+0.00000000e+00j
  7.91928597e-01+2.20994919e-01j  7.91928597e-01-2.20994919e-01j
  7.80296958e-01+0.00000000e+00j  6.29756628e-01+5.04525307e-01j
  6.29756628e-01-5.04525307e-01j  5.70969286e-01+0.00000000e+00j
  4.38193383e-01-1.86937479e-01j  4.38193383e-01+1.86937479e-01j
  2.85061150e-01+0.00000000e+00j  1.32899456e-01+0.00000000e+00j
  1.11682031e-01+1.14457738e-01j  1.11682031e-01-1.14457738e-01j
  5.26261358e-02-3.72524832e-01j  5.26261358e-02+3.72524832e-01j
  1.66070467e-03+0.00000000e+00j  1.37878996e-03+0.00000000e+00j
  5.50298301e-04+3.52582880e-04j  5.50298301e-04-3.52582880e-04j
  2.54662967e-04+1.16662032e-03j  2.54662967e-04-1.16662032e-03j
 -2.77884059e-05+0.00000000e+00j -3.39686567e-04+0.00000000e+00j
 -1.17651733e-03+0.00000000e+00j]
(10000, 25)
